# Read validation data

In [1]:
from read_data_val import read_data_val
validation_pairs, validation_pairs_labels = read_data_val()

Number of validation pairs: 14938
Number of validation positives: 7381
Number of validation negatives: 7557


# Preprocess function

In [2]:
import tensorflow as tf 
def preprocess(image_path):
    # read the file 
    raw = tf.io.read_file(image_path)
    img = tf.io.decode_image(raw, expand_animations=False, channels = 3)
    img = tf.image.resize(img, size = (256,256), preserve_aspect_ratio=True)
    img = tf.image.resize_with_crop_or_pad(img, 224, 224)
    img = tf.cast(img, tf.float32)/255.0       # convert rgb values to between 0 and 1
    return img 

def preprocess_pair(pair):
    imgA = preprocess(pair[0])
    imgB = preprocess(pair[1])
    return (imgA, imgB)


data_augmentation = tf.keras.Sequential([
    tf.keras.layers.RandomFlip("horizontal_and_vertical"),
    tf.keras.layers.RandomRotation((-0.4, 0.4)),
    tf.keras.layers.RandomBrightness(factor=(-0.2, 0.2), value_range=(0., 1.)),
    tf.keras.layers.GaussianNoise(0.005),
    tf.keras.layers.RandomContrast(factor=(0.1, 0.9)),
    tf.keras.layers.RandomTranslation(height_factor=0.2, width_factor=0.2)
])

2025-02-26 15:54:42.396107: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-02-26 15:54:43.890634: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-02-26 15:54:44.541812: E tensorflow/stream_executor/cuda/cuda_blas.cc:2981] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-02-26 15:54:48.164187: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: li

# Load all the final .h5 models

In [3]:
import tensorflow as tf 
from keras import backend as K

MARGIN = 1
def contrastive_loss(y_true, y_pred):
    y_true = tf.cast(y_true, tf.float32)
    square_pred = K.square(y_pred)
    margin_square = K.square(K.maximum(MARGIN - y_pred, 0))
    return (y_true * square_pred + (1 - y_true) * margin_square)

class Custom_Precision(tf.keras.metrics.Precision):

    def update_state(self, y_true, y_pred, sample_weight=None):
        y_pred_fix = tf.math.less(y_pred, 0.5)   # override the default implementation of >= 0.5 by <0.5 (Distance)
        y_pred_fix = tf.cast(y_pred_fix, y_pred.dtype)
       
        return super().update_state(y_true, y_pred_fix, sample_weight)
  
class Custom_Recall(tf.keras.metrics.Recall):

    def update_state(self, y_true, y_pred, sample_weight=None):
        y_pred_fix = tf.math.less(y_pred, 0.5) 
        y_pred_fix = tf.cast(y_pred_fix, y_pred.dtype)
       
        return super().update_state(y_true, y_pred_fix, sample_weight)
  
class Custom_Accuracy(tf.keras.metrics.Accuracy):

    def update_state(self, y_true, y_pred, sample_weight=None):
        y_pred_fix = tf.math.less(y_pred, 0.5) 
        y_pred_fix = tf.cast(y_pred_fix, y_pred.dtype)
       
        return super().update_state(y_true, y_pred_fix, sample_weight)

In [4]:
from keras.models import load_model
import os 

models = [] 
model_str = []
for model in os.listdir("models_h5"):
    model_str.append(model)

# sort the files 
model_str.sort()
for model in model_str:
    this_model = load_model(os.path.join("models_h5", model), custom_objects={
        "contrastive_loss": contrastive_loss,
        "Custom_Precision": Custom_Precision,
        "Custom_Accuracy": Custom_Accuracy,
        "Custom_Recall": Custom_Recall
    })
    models.append(this_model)

# sort the models according to the model_str 
models

# Evaluate the model on validation data
The models have to be loaded one by one otherwise it eventually stops working

In [5]:
def evaluate(model):
    total, correct = 0, 0

    for index, pair in enumerate(validation_pairs):
        imgA, imgB = preprocess_pair(pair)

        # Add batch dimension
        imgA = tf.expand_dims(imgA, axis=0)  # (1, 224, 224, 3)
        imgB = tf.expand_dims(imgB, axis=0)  # (1, 224, 224, 3)

        prediction = model.predict([imgA, imgB])  
        """
        print(f"Distance: {prediction[0]}")
        print(f"Predicted: {prediction[0] <= 0.5}")
        print(f"Label: {bool(validation_pairs_labels[index])}")
        """

        if (bool(validation_pairs_labels[index]) == (prediction[0] <= 0.5)):
            correct += 1
        total += 1

    accuracy = correct/total
    print(total)
    print(correct)
    print(f"Accuracy: {accuracy}")
    

    # return the final accuracy on val data 
    return accuracy

In [13]:
model1 = models[0]
model2 = models[1]
model3 = models[2]
model4 = models[3]
model5 = models[4]
model6 = models[5]
model7 = models[6]
model8 = models[7]

accuracy_list = []
accuracy_list_test = []

In [7]:
accuracy_list.append(evaluate(model1))

2025-02-24 18:15:17.274425: I tensorflow/stream_executor/cuda/cuda_dnn.cc:384] Loaded cuDNN version 8100
2025-02-24 18:15:17.698589: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2025-02-24 18:15:17.698982: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2025-02-24 18:15:17.699006: W tensorflow/stream_executor/gpu/asm_compiler.cc:80] Couldn't get ptxas version string: INTERNAL: Couldn't invoke ptxas --version
2025-02-24 18:15:17.699392: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2025-02-24 18:15:17.699423: W tensorflow/stream_executor/gpu/redzone_allocator.cc:314] INTERNAL: Failed to launch ptxas
Relying on driver to perform ptx compilation. 
Modify $PATH to customize ptxas location.
This message will be only logged once.


1/1 [==============================] - 0s 16ms/step


2025-02-24 18:15:17.988009: I tensorflow/stream_executor/cuda/cuda_blas.cc:1614] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.


1/1 [==============================] - 0s 16ms/step
14938
11846
Accuracy: 0.7930111125987415


In [8]:
accuracy_list.append(evaluate(model2))

1/1 [==============================] - 0s 17ms/step
14938
11880
Accuracy: 0.7952871870397643


In [9]:
accuracy_list.append(evaluate(model3))

1/1 [==============================] - 0s 17ms/step
14938
11346
Accuracy: 0.7595394296425224


In [10]:
accuracy_list.append(evaluate(model4))

1/1 [==============================] - 0s 15ms/step
14938
11887
Accuracy: 0.7957557906011514


In [11]:
accuracy_list.append(evaluate(model5))

1/1 [==============================] - 0s 15ms/step
14938
11717
Accuracy: 0.784375418396037


In [12]:
accuracy_list.append(evaluate(model6))

1/1 [==============================] - 0s 17ms/step
14938
11678
Accuracy: 0.7817646271254519


In [13]:
accuracy_list.append(evaluate(model7))

1/1 [==============================] - 0s 16ms/step
14938
8682
Accuracy: 0.5812023028517874


In [14]:
accuracy_list.append(evaluate(model8))

1/1 [==============================] - 0s 15ms/step
14938
11630
Accuracy: 0.7785513455616548


In [15]:
print("Models: " + str(model_str))
print("Accuracy: " + str(accuracy_list))

Models: ['final1.h5', 'final2.h5', 'final3.h5', 'final4.h5', 'final5.h5', 'final6.h5', 'final7.h5', 'final8.h5']
Accuracy: [0.7930111125987415, 0.7952871870397643, 0.7595394296425224, 0.7957557906011514, 0.784375418396037, 0.7817646271254519, 0.5812023028517874, 0.7785513455616548]


# Evaluate on test data

In [5]:
from read_data_test import read_data_test

custom_test_data = read_data_test()

def evaluate_test(model):
    THRESHOLD = 0.5

    total = 0
    correct = 0
    false_positive = 0
    false_negative = 0

    total_positive = 0
    positive_correct = 0
    total_negative_easy = 0
    negative_easy_correct = 0
    total_negative_hard = 0
    negative_hard_correct = 0

    for ia, ib, label in custom_test_data:
        pa = preprocess(ia)
        pb = preprocess(ib)

        # Add batch dimension
        imgA = tf.expand_dims(pa, axis=0)  # (1, 224, 224, 3)
        imgB = tf.expand_dims(pb, axis=0)  # (1, 224, 224, 3)

        prediction = model.predict([imgA, imgB])  
  
        truth = bool(label)
        predicted_label = prediction[0] <= THRESHOLD
        if (truth == predicted_label):
            correct += 1
        else:
            if not truth and predicted_label:
                false_positive += 1
            elif truth and not predicted_label:
                false_negative += 1 

        # determine if the sample is positive, negative easy or negative hard
        if ia.split("/")[1] == "positive":
            total_positive += 1
            if truth == predicted_label:
                positive_correct += 1
        if ia.split("/")[1] == "negative_easy":
            total_negative_easy += 1
            if truth == predicted_label:
                negative_easy_correct += 1
        if ia.split("/")[1] == "negative_hard":
            total_negative_hard += 1
            if truth == predicted_label:
                negative_hard_correct += 1

        # increment total count
        total += 1

    # currently only return the accuracy
    return correct/total

In [14]:
accuracy_list_test.append(evaluate_test(model1))
accuracy_list_test.append(evaluate_test(model2))
accuracy_list_test.append(evaluate_test(model3))
accuracy_list_test.append(evaluate_test(model4))
accuracy_list_test.append(evaluate_test(model5))
accuracy_list_test.append(evaluate_test(model6))
accuracy_list_test.append(evaluate_test(model7))
accuracy_list_test.append(evaluate_test(model8))

1/1 [==============================] - 0s 14ms/step


In [15]:
print("Models: " + str(model_str))
print("Accuracy: " + str(accuracy_list_test))

Models: ['final1.h5', 'final2.h5', 'final3.h5', 'final4.h5', 'final5.h5', 'final6.h5', 'final7.h5', 'final8.h5']
Accuracy: [0.75, 0.65, 0.575, 0.7, 0.575, 0.7, 0.375, 0.575]
